In [ ]:
# @title PIP
%pip install opencv-python==4.8.0.76
%pip install pytesseract==0.3.9

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
# @title TESTES ):D
main()





##Versão nova

In [33]:
import pytesseract
import regex as re
import numpy as np
import cv2
#from google.colab.patches import cv2_imshow
from PIL import ImageFont, ImageDraw, Image
import re
import os

pytesseract.pytesseract.tesseract_cmd = r'C:\Program Files\Tesseract-OCR\tesseract.exe'

tipo_conta = None
n_conta = None
mes_referencia = None
vencimento = None
emisao = None
cpf = None
periodo = None
valor_vencimento = None

def list_files_in_directory(folder_path):
    files_array = []
    for root, dirs, files in os.walk(folder_path):
        for file in files:
            file_path = os.path.join(root, file)
            files_array.append(file_path)
    return files_array

def descobre_prestadora(documento):
  if re.findall('^[Cc][Ll][Aa][Rr][Oo]', documento,  re.MULTILINE):
        prestadora = 'Claro'
  elif re.findall('^[Tt][Ii][Mm]', documento,  re.MULTILINE):
        prestadora = 'Tim'
  elif re.findall('^[Vv][Ii][Vv][Oo]', documento, re.MULTILINE):
        prestadora = 'Vivo'
  else:
        prestadora = None

  return prestadora

def extrair_info(documento, prestadora):
  if prestadora == 'Vivo':
    #PIPELINE VIVO
    tipo_conta = 'Telefonia'

    n_conta = re.findall(r'[Cc][Oo][Nn][Tt][Aa](.*[\r\n].*)(\b\d{9}\b)', documento, re.MULTILINE)

    #TEM VERSÃO COM TEXTO NO DIA DO MES , VERIFICAR ISSO
    #Notas para o paper, esse regex foi complexa de confecionar, a diferença entre o bloco de texto que a geente procurava era "referencia:" ou "referencia "
    mes_referencia = re.find(r"[Rr][Ee][Ff][Ee][Rr][Êê|Ee][Nn][Cc][Ii][Aa][\:\s|\s](.*?)(0[1-9]|1[0-2])/(19|20)\d{2}", documento, re.MULTILINE)
    #mes_referencia = pre_mes_referencia[1]

    #VENCIMENTO PODE NÃO SER POSSIVEL
    vencimento =  re.findall(r'((.|\n)*?)\b(0[1-9]|1[0-2])\/(19|20[0-9]{2})\b', documento, re.MULTILINE)

    emisao = re.findall(r'[Dd][ÁáAa][Tt][Aa]\s[Dd][Ee] [Ee][Mm][IiÍí][Ss][Ss][ÃãAaÃa][OoOo]\s(0[1-9]|[12][0-9]|3[01])/(0[1-9]|1[0,1,2])/(19|20)\d{2}', documento, re.MULTILINE)

    cpf = encontra_cpf_cnpj(documento)

    periodo = re.findall(r'(P|p)(E|e)(R|r)(Í|í)(O|o)(D|d)(O|o)\s\:.*?\n((0[1-9]|[12][0-9]|3[01])\/(0[1-9]|1[0,1,2])\/(19|20)\d{2})', documento, re.MULTILINE)

    valor_vencimento = None


  elif prestadora == 'Claro':

    regex_n_conta = r'[Cc][Oo][Nn][Tt][Aa](.*[\r\n].*)(\b\d{9}\b)'

    # Regex para encontrar a data de vencimento
    regex_data_vencimento = r'\b(\d{2}/\d{2}/\d{4})\b'

    # Regex para encontrar a data de início
    regex_data_inicio = r'\b(\d{2}/\d{2}/\d{4})\b'

    # Regex para encontrar o valor total
    regex_valor_total = r'\b(\d+,\d{2})\b'


    #PIPELINE CLARO

    tipo_conta = 'Telefonia'



    pre_n_conta = re.findall(regex_n_conta, documento, re.MULTILINE)
    n_conta = pre_n_conta[0][1]

    pre_mes_referencia = re.findall(regex_data_vencimento, documento, re.MULTILINE)
    mes_referencia = pre_mes_referencia[0]

    vencimento =  re.findall(r'[Vv][Ee][Nn][Cc][Ii][Mm][Ee][Nn][Tt][Oo]\s(0[1-9]|[12][0-9]|3[01])/(0[1-9]|1[0,1,2])/(19|20)\d{2}', documento, re.MULTILINE)

    emisao = re.findall(regex_data_inicio, documento, re.MULTILINE)

    cpf = encontra_cpf_cnpj(documento)

    periodo = None

    valor_vencimento = re.findall(regex_valor_total, documento, re.MULTILINE)

  elif prestadora == 'Tim':
    #PIPELINE TIM
    pass

  print(prestadora)
  print(tipo_conta)
  print(n_conta)
  print(mes_referencia)
  print(vencimento)
  print(emisao)
  print(cpf)
  print(periodo)
  print(valor_vencimento)

  return prestadora, tipo_conta, n_conta, mes_referencia, vencimento, emisao, cpf, periodo, valor_vencimento

def encontra_cpf_cnpj(documento):
  tipo = 'CNPJ'
  dado = re.findall(r"[Cc][Pp][Ff]\/[Cc][Nn][Pp][Jj].*?:.*?(?=\d)(.*?(?=\d)([0-9]{3}\.?[0-9]{3}\.?[0-9]{3}\-?[0-9]{2}))", documento, re.MULTILINE)
  return dado #dado[0][0]

def main(arg):
  fonte = '/content/drive/MyDrive/Colab Notebooks/Fonte/Calibri/Calibri.ttf'


  #paths = ['C:\_CONTAS_COLETADAS\separados\claro-03-2023-johnathan\claro-03-2023-johnathan-page1.png']
  #paths = ['/content/page0.png','/content/page1.png','/content/page2.png']
  #paths = ['/content/drive/MyDrive/_TCC/Contas_coletadas/output-final/vivo-08-2023-cintia-page1.png']
  path = arg
  paths = list_files_in_directory(path)
  documento = ''

  for i, pdfs in enumerate(paths):
    img = cv2.imread(paths[i])
    convertido = pytesseract.image_to_string(img, lang = 'por', config='--psm 3')
    documento += convertido
    print(documento)

  #PEGA PRESTADORA
  prestadora = descobre_prestadora(documento)
  infos = extrair_info(documento, prestadora)

  return infos
  # Método de instância para exibir informações da conta


In [35]:

all_data = []

data = main('C:\_CONTAS_COLETADAS')


all_data.append(data)

Seu número Claro
11 97056 2915

ANA JULIA PIMENTEL GONCALVES Período de uso Vencimento
REROFESSOR NOBIL MARCACINI 200 de 17/01/2023 a 16/02/2023 08/03/2023
JARAGUA Veja aqui o que está sendo cobrado:

02998-080 SAO PAULO SP 1. Plano Contratado R$ 95,70

Claróí clube Saldo de pontos em 14/02/23 1.423 Total a pagar

Pontos resgatados em 31/01 0

MENSAGENS IMPORTANTES: CANAIS DE ATENDIMENTO:

Caro cliente, de acordo com os termos do regulamento e contrato do seu pla- Acesse sua conta e outros serviços:

no, a alteração anual programada do valor promocional foi atualizada, e a No app Minha Claro / No Whatsapp 11999910621

Claro valorizando esse relacionamento, optou por bonificá-lo com mais inter- Na internet - minhaclaro.com.br

net. Confira os detalhes em claro.com.br/alteracaoplano2022 ou no App Pelo celular *1052% / No Atendimento Claro 1052 / Ouvidoria - Ligue 08007010180
Minha Claro Fatura em braile ligue 1052 | Deficiente auditivo ou surdo acesse www.claro.com.br/minha-claro

1. PLA

In [ ]:

import pandas as pd


df = pd.DataFrame(all_data, columns=["prestadora", "tipo_conta", "n_conta", "mes_referencia", "vencimento", "emisao", "cpf", "periodo", "valor_vencimento"])


excel_file = "dados_contas.xlsx"


df.to_excel(excel_file, index=False, engine='openpyxl')

print(f'Dados foram salvos em {excel_file}')